In [1]:
import requests
import re
import time

import pandas as pd
import lxml
from bs4 import BeautifulSoup

pd.options.display.max_rows = 4000

In [2]:
URL = 'https://www.searchfunder.com'

session = requests.session()

front = session.get(URL)
csrf_token = re.findall(r'<input type="hidden" name="_token" value="(.*)"', 
front.text)[0]

cookies = session.cookies

payload = {
    'email': '#your email here',
    'password': '# your password here',
    '_token': csrf_token,
}

r = requests.post(URL + '/auth/login', data=payload, cookies=cookies)


In [3]:
searchfunds_HTML = requests.get(URL + '/searchfund/allsearchfunds', cookies=r.cookies)

In [4]:
datasearchfund_id = re.findall('data-searchfund_id="[0-9]+"',searchfunds_HTML.text)
searchfund_data_index = list(map(int,re.findall('[0-9]+',str(datasearchfund_id))))

In [5]:
table = pd.read_html(searchfunds_HTML.text)
searchfunds = table[0][table[0]['name'].notna()]
searchfunds = searchfunds.reset_index()
searchfunds.index = searchfund_data_index
cols = [0,1]
searchfunds.drop(searchfunds.columns[cols], axis=1,inplace=True)
#searchfunds.to_csv("searchfund_raw2.csv")

In [6]:
#enrichment = []

In [7]:
#enrichment

In [8]:
#enrichment.loc[enrichment['searchfund_index'] == 10]

In [9]:
type(searchfund_data_index[-1])

int

In [10]:
enrichment = []
for index in searchfund_data_index:
    print(index)
    data = requests.get(URL + '/searchfund/ajaxsearchfundrow/'+str(index), cookies=r.cookies)
    time.sleep(0.05)
    soup = BeautifulSoup(data.content, 'html.parser')
    
    ## Get company info
    company_rows=soup.find_all(class_="col-md-3")
    try:
        searchWebsite = re.split(r'\t+',company_rows[0].text)[1].strip('\n')
    except:
        searchWebsite = ""
    try:
        companyWebsite= re.split(r'\t+',company_rows[1].text)[1].strip('\n')
    except:
        companyWebsite=""
    try:
        industry = re.split(r'\t+',company_rows[2].text)[1].strip('\n')
    except:
        industry=""
    try:
        location = re.split(r'\t+',company_rows[3].text)[1].strip('\n')
    except:
        location=""

    
    
    ## Get Searcher info
    searchers=[]
    try:
        searcher_rows=soup.find_all(class_="col-md-12")[0]
        for searcher_row in searcher_rows:
            try:
                searchers.append(re.split(r'\t+',searcher_row.text)[-1].strip('\n'))
            except:
                searchers.append("")
        searchers = list(filter(None, searchers))
    except:
        searchers


    ## Get Investor info
    investors=[]
    try:
        investor_rows=soup.find_all(class_="col-md-12")[2]
        for investor_row in investor_rows:
            try:
                investors.append(re.split(r'\t+',investor_row.text)[-1].strip('\n'))
            except:
                investors.append("")
        investors = list(filter(None, investors))
    except:
        investors

    ## Get Associate info
    associates=[]
    try:
        associate_rows=soup.find_all(class_="col-md-12")[4]
        for associate_row in associate_rows:
            try:
                associates.append(re.split(r'\t+',associate_row.text)[-1].strip('\n'))
            except:
                associates.append("")
        associates = list(filter(None, associates))
    except:
        associates
    
    enrichmentData = {'searchfund_index': index, 'searchWebsite': searchWebsite,'companyWebsite': companyWebsite,'industry':industry,'location':location,'searchers':searchers,'investors':investors,'associates':associates}
    #print(enrichmentData)
    enrichment.append(enrichmentData)
    
    

420
496
501
418
430
415
579
419
407
679
417
423
421
558
958
807
416
268
688
673
63
557
410
1024
422
1023
489
389
260
414
689
429
1022
682
568
411
270
498
478
362
413
509
674
35
425
432
559
443
984
346
505
412
707
219
1071
305
431
309
482
135
870
183
146
277
995
207
283
488
854
609
406
481
387
849
473
161
222
200
215
390
470
220
484
466
1055
681
446
372
334
279
510
474
1027
467
201
284
1025
337
67
351
694
273
383
80
282
840
278
81
185
357
174
124
196
462
395
1258
409
534
364
453
335
216
593
527
15
187
586
195
665
454
38
465
331
154
1353
212
330
355
188
184
836
255
127
84
690
691
829
159
336
143
118
125
732
521
265
700
459
199
452
122
339
312
992
528
460
511
333
319
523
944
468
490
181
1266
78
358
180
194
888
526
203
571
193
1058
164
128
65
356
332
62
385
140
439
655
121
123
572
262
173
269
263
137
82
182
48
313
684
261
258
66
354
437
120
19
338
158
160
26
16
946
310
54
134
83
117
253
560
79
23
254
817
21
30
317
3
177
838
1
46
31
59
702
115
109
483
1777
289
1495
111
1378
451
347
436
850


1513
1769
2025
1002
1514
2026
491
747
1259
1515
1771
2027
236
1260
1516
1772
493
749
1005
1261
1517
1773
2029
494
750
1006
1262
1518
1774
2030
239
495
1007
1263
1519
1775
2031
240
752
1008
1520
1776
2032
497
1265
1521
754
1010
1522
1778
2034
243
499
755
1011
1267
1523
1779
2035
756
1012
1524
1780
2036
1269
1525
2037
502
1270
1526
1782
2038
759
1271
1527
1783
2039
248
760
1272
1528
1784
2040
249
1273
1529
1785
2041
762
1018
1274
1530
1786
2042
507
763
1019
1275
1531
1787
2043
252
508
1020
1276
1532
1788
2044
765
1021
1277
1533
1789
766
1534
1790
2046
767
1535
1791
2047


In [11]:
enrichmentDF = pd.DataFrame(enrichment)


In [12]:
data = requests.get(URL + '/searchfund/ajaxsearchfundrow/6', cookies=r.cookies)

In [13]:
soup = BeautifulSoup(data.content, 'html.parser')

In [14]:
## Get company info
company_rows=soup.find_all(class_="col-md-3")
try:
    searchWebsite = re.split(r'\t+',company_rows[0].text)[1].strip('\n')
except:
    searchWebsite = ""
try:
    companyWebsite= re.split(r'\t+',company_rows[1].text)[1].strip('\n')
except:
    companyWebsite=""
try:
    industry = re.split(r'\t+',company_rows[2].text)[1].strip('\n')
except:
    industry=""
try:
    location = re.split(r'\t+',company_rows[3].text)[1].strip('\n')
except:
    location=""
    
    
## Get Searcher info
searchers=[]
try:
    searcher_rows=soup.find_all(class_="col-md-12")[0]
    for searcher_row in searcher_rows:
        try:
            searchers.append(re.split(r'\t+',searcher_row.text)[-1].strip('\n'))
        except:
            searchers.append("")
    searchers = list(filter(None, searchers))
    print(searchers)
except:
    searchers
    
    
## Get Investor info
investors=[]
try:
    investor_rows=soup.find_all(class_="col-md-12")[2]
    for investor_row in investor_rows:
        try:
            investors.append(re.split(r'\t+',investor_row.text)[-1].strip('\n'))
            index= index +1
        except:
            investors.append("")
    investors = list(filter(None, investors))
    print(investors)
except:
    investors
    
## Get Associate info
associates=[]
try:
    associate_rows=soup.find_all(class_="col-md-12")[4]
    for associate_row in associate_rows:
        try:
            associates.append(re.split(r'\t+',associate_row.text)[-1].strip('\n'))
        except:
            associates.append("")
    associates = list(filter(None, associates))
    print(associates)
except:
    associates

['Josh\xa0Bilmes']
['Isaac\xa0Chalal ', 'Timur\xa0Colak ', 'Ralph\xa0Lawson ', "David\xa0O'Shaughnessey", 'Maja\xa0Silwinski ', 'Clint\xa0Smith ', 'William  "Bill"\xa0Wallach ']


In [15]:
enrichmentDF


searchfund_index                                      searchWebsite  \
0                  420                                                      
1                  496                                                      
2                  501                                                      
3                  418                                                      
4                  430                                                      
5                  415                                                      
6                  579                                        sverica.com   
7                  419                                                      
8                  407                                                      
9                  679                                                      
10                 417                                                      
11                 423                                                      
12                 421                                                      
13                 558                                                      
14                 958                                                      
15                 807                                                      
16                 416                                                      
17                 268                                                      
18                 688                                                      
19                 673                                                      
20                  63                  http://www.gulfsearchcapital.com/   
21                 557  inactive: http://www.millenniumv.com/our-firm/...   
22                 410                                                      
23                1024                                                      
24                 422                                                      
25                1023                                                      
26                 489                          http://www.falckholt.com/   
27                 389                     http://www.rockwoodequity.com/   
28                 260                   http://www.blackfordcapital.com/   
29                 414                                                      
30                 689                                                      
31                 429                                                      
32                1022                                                      
33                 682                                                      
34                 568                               http://www.scven.com   
35                 411                                                      
36                 270                    http://www.tetonindustries.com/   
37                 498                                                      
38                 478                                                      
39                 362                          http://www.mira-blau.com/   
40                 413                                                      
41                 509                                                      
42                 674                                                      
43                  35                                                      
44                 425                        http://www.apcpartners.com/   
45                 432                                                      
46                 559                  https://informationprotected.com/   
47                 443                                                      
48                 984                                                      
49                 346                                                      
50                 505                      http://www.argo-partners.com/   
51

In [16]:
#searchfunds = pd.merge([searchfunds, enrichment], how='right',on='searchfund_index')

merged = pd.merge(searchfunds, enrichmentDF, left_index=True, right_on='searchfund_index')
merged

name                type  \
0           Nova Capital  |Jim Southern||Irv Grousbeck|      Single Sponsor   
1     Galena Corp  Harvard University - Harvard Busi...         Traditional   
2     Hanover West  |Paul Centenari ||Peter Centenari |         Traditional   
3     David Dodson - 1st Fund  Stanford University -...         Traditional   
4     Balkin Corp  Stanford University|Stanford Univ...         Traditional   
5     Braden Partners  |Peter Kelly||Leon Winters||P...         Traditional   
6     Sverica International  |Sandro Mina||Martin St...         Traditional   
7     Pathfinder Capital  |Larry Stevenson ||Harry Y...         Self Funded   
8     Amersham Corp.  Harvard University - Harvard B...         Traditional   
9            Simon Webster Search Fund  |Simon Webster|         Traditional   
10    Falcon Capital Corp. |David Dodson||Jeff Steve...         Traditional   
11    Mill River Corporation |Kevin Taweel||Jim Elli...         Traditional   
12                Gene Baker Search Fund  |Gene Baker |         Traditional   
13    Sansair Corporation  |Karen Moriarty||William ...         Traditional   
14    Redwood Partners, Inc.  |John Moran ||William ...         Traditional   
15                        The Nexus Group  |Doug Wells|         Traditional   
16                      Russell Poore  |Russell Poore |         Self Funded   
17       Presidio Partners  |Doug Tudor ||Nick Mansour|         Traditional   
18           Jim Southern Search Fund 2  |Jim Southern|         Traditional   
19           Ancora Capital |Jeff Stevens||Gerald Chew|         Traditional   
20    Gulf Search Capital  |Patrick Mansfield||Larry...         Self Funded   
21    Al Kapoor - Search Fund  |Al Kapoor ||Howard S...         Traditional   
22                      Gregory Mazur  |Gregory Mazur |         Self Funded   
23    First American Records Management Company (FAR...         Traditional   
24     Circle Point Capital Corporation  |Dale Blocher|         Traditional   
25    Tony Distefano Search Fund  |Tony Distefano ||...         Traditional   
26    Falck Holt  |Lee Falck ||Bobby Holt ||Rob Mark...         Traditional   
27                      Rockwood Equity  |Brett Keith |         Self Funded   
28    Blackford Capital  Harvard University - Harvar...         Traditional   
29        Mike and Linda Katz |Linda Katz ||Mike Katz |         Self Funded   
30    Jim Southern Search Fund 3  |Jim Southern||Sco...         Traditional   
31    Aragon Capital  London Business School|Univers...         Traditional   
32    Pratap Mukherjee & Brian Haas Serach Fund  |Pr...         Traditional   
33     Michael Sanabria Search Fund  |Michael Sanabria|         Self Funded   
34            SC Ventures  |Pankaj Amin||Elaine Boxer |         Traditional   
35    Montebello Capital  |John Fowler ||Josh Greenb...         Traditional   
36    Teton Industries  |John VanNewkirk ||Craig Bur...         Traditional   
37                 Genesis Ventures  |Yosufi Tyebkhan |         Self Funded   
38    Crystal Springs Capital, LLC  |David Kennedy |...         Traditional   
39    Mirablau Equity & Services GmbH  |Jürgen Rilli...         Self Funded   
40                                             Julie Ha         Traditional   
41    Leader Creek Partners  |Chris Cunning||Peter D...         Traditional   
42                       Dionis Company  |Jeff Stevens|         Traditional   
43    Eventide Management  Colgate University|Stanfo...         Traditional   
44    AP Capital Partners  |Richard Powell||Frantz A...         Traditional   
45    Rabbit Creek Partners, LLC  |Doren Spinner ||J...         Traditional   
46    Access CIG  |Dennis Barnedt ||Aaron Gabbart||J...      Single Sponsor   
47    Liffey Thames Group, LLC  |Christian Lawrence|...         Traditional   
48    Altos Andes  |Carlos Fell ||Cristóbal Lira ||G...         Traditional   
49    Argo Investors LLC  Princeton University|Jason...         Traditional   
50    Argo Management 

In [17]:
merged['name'] = merged['name'].str.split("|", n = 1, expand = True)[0]
merged['formed'] = merged['formed'].str.split(" ", n = 1, expand = True)[0]
merged['acquired'] = merged['acquired'].str.split(" ", n = 1, expand = True)[0]

In [18]:
#merged['formed'] = pd.to_datetime(merged['formed'].dropna, format='%Y%m%d')
merged

name                type  \
0                                        Nova Capital        Single Sponsor   
1     Galena Corp  Harvard University - Harvard Busi...         Traditional   
2                                        Hanover West           Traditional   
3     David Dodson - 1st Fund  Stanford University -...         Traditional   
4                      Balkin Corp  Stanford University         Traditional   
5                                     Braden Partners           Traditional   
6                               Sverica International           Traditional   
7                                  Pathfinder Capital           Self Funded   
8     Amersham Corp.  Harvard University - Harvard B...         Traditional   
9                           Simon Webster Search Fund           Traditional   
10                                Falcon Capital Corp.          Traditional   
11                              Mill River Corporation          Traditional   
12                             Gene Baker Search Fund           Traditional   
13                                Sansair Corporation           Traditional   
14                             Redwood Partners, Inc.           Traditional   
15                                    The Nexus Group           Traditional   
16                                      Russell Poore           Self Funded   
17                                  Presidio Partners           Traditional   
18                         Jim Southern Search Fund 2           Traditional   
19                                      Ancora Capital          Traditional   
20                                Gulf Search Capital           Self Funded   
21                            Al Kapoor - Search Fund           Traditional   
22                                      Gregory Mazur           Self Funded   
23    First American Records Management Company (FAR...         Traditional   
24                   Circle Point Capital Corporation           Traditional   
25                         Tony Distefano Search Fund           Traditional   
26                                         Falck Holt           Traditional   
27                                    Rockwood Equity           Self Funded   
28    Blackford Capital  Harvard University - Harvar...         Traditional   
29                                 Mike and Linda Katz          Self Funded   
30                         Jim Southern Search Fund 3           Traditional   
31               Aragon Capital  London Business School         Traditional   
32          Pratap Mukherjee & Brian Haas Serach Fund           Traditional   
33                       Michael Sanabria Search Fund           Self Funded   
34                                        SC Ventures           Traditional   
35                                 Montebello Capital           Traditional   
36                                   Teton Industries           Traditional   
37                                   Genesis Ventures           Self Funded   
38                       Crystal Springs Capital, LLC           Traditional   
39                    Mirablau Equity & Services GmbH           Self Funded   
40                                             Julie Ha         Traditional   
41                              Leader Creek Partners           Traditional   
42                                     Dionis Company           Traditional   
43              Eventide Management  Colgate University         Traditional   
44                                AP Capital Partners           Traditional   
45                         Rabbit Creek Partners, LLC           Traditional   
46                                         Access CIG        Single Sponsor   
47                           Liffey Thames Group, LLC           Traditional   
48                                        Altos Andes           Traditional   
49             Argo Investors LLC  Princeton University         Traditional   
50                    

In [19]:
merged.to_csv("searchfund_allV3.csv")

In [20]:
searchfunds.loc[10]

name        Gold Coast Partners  Harvard University - Harv...
type                                              Traditional
formed                                     20160501  May 2016
location                                         Accra, Ghana
stage                                                   Raise
company                                                   NaN
acquired                                                  NaN
Name: 10, dtype: object

In [21]:
ndcaTable = pd.DataFrame(None)
for index in range(0,9): 
    ndcaURL = 'https://nadca.com/find-a-professional?distance%5Bpostal_code%5D=&distance%5Bcountry%5D=us&distance%5Bsearch_distance%5D=100&distance%5Bsearch_units%5D=mile&province=All&country=us&title=&emp_admin_first_name=&emp_admin_last_name=&title_1=&field_company_admin_value=&field_employee_certification_tid=All&field_company_job_type_tid=All&field_company_services_tid=All&items_per_page=100&page='+str(index)
    ndcaData = requests.get(ndcaURL)
    ndcaTable = ndcaTable.append(pd.read_html(ndcaData.text)[0])





In [22]:
ndcaTable

0  \
0               Sani-Vac Service, Inc.  United States   
1   Sani-Vac Service, Inc. 5750 Enterprise Ct Warr...   
2   Dyna-Kleen Services Inc. 4540 S 79th St Omaha,...   
3   Safety King, Inc. 50000 Ryan Rd Shelby Townshi...   
4   Air Care Services 1504 Ogden Ave Lisle, Illino...   
5   Mr. Power Clean, Inc. W5021 Amy Ave Ste 8 Kauk...   
6   Airways Systems, Inc. 1100 Tower Ln Bensenvill...   
7   CSC Services, LLC -- Connecticut Steam Cleanin...   
8   Clean Air Systems of LA, Inc. PO Box 6210 Shre...   
9   EnviroVantage 10 Spencer St Stoneham, Massachu...   
10  Scientific Environmental Services Co. 5459 43r...   
11  Riteway Duct Cleaning Services, Inc. 5110D Col...   
12  Industrial Power Clean, Inc. 281 Greenwood Ave...   
13  Southwest Air Duct Cleaning 11385 James Watt D...   
14  Air Duct Cleaning Co./Machado Environmental Co...   
15  National Air Duct Maintenance Corp. 439 N West...   
16  Duct & Vent Cleaning of America, Inc. 311 Page...   
17  Armstrong Duct, Vent, Hearth & Home 531 Front ...   
18  Kleen Air Service Corporation 5354 N Northwest...   
19  Brouwer Bros. Steamatic 4120 W 123rd St Alsip,...   
20  Cochrane Ventilation, Inc. 220 Ballardvale St ...   
21  DUCTZ of Tampa Bay 3055 47th Ave N Saint Peter...   
22  Monster Vac, Inc. 3970 S Decatur St Ste F Engl...   
23  United Safety Services, Inc. 420 E Main St Car...   
24  Chemiclene, Inc. 22 W Price St Linden, New Jer...   
25  Service-Tech Corporation 7589 First Pl Clevela...   
26  D.J. Cross, Inc. 2 Old Pennell Rd Media, Penns...   
27  Champion Cleaning Specialists, Inc. 8391 Blue ...   
28  Phoenix Industrial Cleaning, Inc. 5380 McDermo...   
29  Weather Engineers & Envirovac, Inc. PO Box 370...   
30  Chemical Specifics, Inc. 4609 54th Rd Maspeth,...   
31  Olympia Maintenance, Inc. 3025 W Soffel Ave Me...   
32  Breathe-Easy Air Duct Cleaning /Clean Dean's C...   
33  Dusty Ducts, Inc. 1076 Corporate Park Dr Fores...   
34  LCS Kleen-Aire, Inc. 3210 S Scenic Ave Springf...   
35  The Mad Hatter 5250 Atlanta Hwy Alpharetta, Ge...   
36  Dalton Environmental Cleaning Corp. PO Box 379...   
37  Ductworks, Inc. 5535 W 56th Ave Unit 100 Arvad...   
38  Gillit's Duct Cleaning, Inc. 719 Gardina San A...   
39  Power Vac America, Inc. 6613 Springer St Houst...   
40  Nelbud 360 51 Koweba Ln Indianapolis, Indiana ...   
41  Interior Maintenance Company, Inc. 45 Scottdal...   
42  American Clean Air, Inc. PO Box 475 North Pemb...   
43  Steamatic of Colorado Springs 2616 Verde Dr Co...   
44  Action Duct Cleaning 2333 Lincoln Ave Altadena...   
45  Delta Industrial Services 5562 Tuxedo Rd Hyatt...   
46  DUCTZ of South Louisiana 121 Luke Dr Lafayette...   
47  Providet Service Associates, Inc. 50 Division ...   
48  Hoover's Air Duct Cleaning, Inc. 8201 Ville Ct...   
49  Air Maintenance, Inc. W230N4933 Betker Dr Pewa...   
50  Mechanical Services of Central Florida 9820 Sa...   
51  Indoor Air Professionals, Inc. 800 Commerce Pk...   
52  Cunningham Duct Cleaning Co., Inc. 869 Sylvan ...   
53  ABC Cleaning, Inc. 809 Eyrie Dr Oviedo, Florid...   
54  Ductz of Greater Orlando 3761 Silver Star Rd O...   
55  In-Viro Care PO Box 194673 San Juan, Puerto Ri...   
56  Aero Filter, Inc. 1604 E Avis Dr Madison Heigh...   
57  Americlean Service Corporation 9201 Enterprise...   
58  Mintie, LLC 1114 N San Fernando Rd Los Angeles...   
59  Duct Doctor USA 5555 Oakbrook Pkwy Ste 660 Nor...   
60  McAfee Air Duct Cleaning 4750 Hempstead Statio...   
61  Air Quality Systems, Inc. 5925 Peachtree Cors ...   
62  Americlean, Inc. 1565 E 91st Ave Merrillville,...   
63  The Butlers & Air Quality Control Systems 1661...   
64  Midwest Duct Cleaning Services 9111 W 51st Ter...   
65  McCoy Plumbing, Heating and Cooling 103 S Main...   
66  Schoen Duct Cleaning 704 Cooper St Edgewater P...   
67  Guardian Power Cleaning, Inc. 8 W Main St Ste ...   
68  Ventilation Power Cleaning Inc. 3914 Leary Way...   
69  Air-Tek of Tuscaloosa LLC 912 29th Ave Tuscalo...   
70  S